In [1]:
import keras as k
import scipy
import pickle

from keras import optimizers
from sklearn.utils import shuffle



Using Theano backend.


In [2]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.preprocessing import StandardScaler
from keras.callbacks import ModelCheckpoint, EarlyStopping
from keras.models import model_from_json

from keras.models import Sequential
from keras.layers import Dense, Activation
import pickle
import matplotlib.pyplot as plt
%matplotlib inline

In [3]:
home = '/home/nandhini/aozel/periodicBox'
phi = 0.1
data_signature1 = 'fsize' + str(9)+'phi'+str(phi)+'dp'+str(75)+'timestep'+str(0.6)
data_signature2 = 'fsize' + str(9)+'phi'+str(phi)+'dp'+str(75)+'timestep'+str(0.7)
data_signature3 = 'fsize' + str(5)+'phi'+str(phi)+'dp'+str(75)+'timestep'+str(0.525)
data_signature4 = 'fsize' + str(11)+'phi'+str(phi)+'dp'+str(75)+'timestep'+str(0.55)
data_signature5 = 'fsize' + str(9)+'phi'+str(phi)+'dp'+str(150)+'timestep'+str(0.6)
data_signature6 = 'fsize' + str(9)+'phi'+str(phi)+'dp'+str(300)+'timestep'+str(0.65) 




file_myData1 = "corrected_myDataFSUslip"+data_signature1+".pickle"
file_myData2 = "corrected_myDataFSUslip"+data_signature2+".pickle"
file_myData3 = "corrected_myDataFSUslip"+data_signature3+".pickle"
file_myData4 = "corrected_myDataFSUslip"+data_signature4+".pickle"
file_myData5 = "corrected_myDataFSUslip"+data_signature5+".pickle"
file_myData6 = "corrected_myDataFSUslip"+data_signature6+".pickle"





file_target1 = "corrected_targetFSUslip"+data_signature1+".pickle"
file_target2 = "corrected_targetFSUslip"+data_signature2+".pickle"
file_target3 = "corrected_targetFSUslip"+data_signature3+".pickle"
file_target4 = "corrected_targetFSUslip"+data_signature4+".pickle"
file_target5 = "corrected_targetFSUslip"+data_signature5+".pickle"
file_target6 = "corrected_targetFSUslip"+data_signature6+".pickle"




myData1 = pickle.load( open( file_myData1, "rb" ) )
myData2 = pickle.load( open( file_myData2, "rb" ) )
myData3 = pickle.load( open( file_myData3, "rb" ) )
myData4 = pickle.load( open( file_myData4, "rb" ) )
myData5 = pickle.load( open( file_myData5, "rb" ) )
myData6 = pickle.load( open( file_myData6, "rb" ) )


myData = np.vstack((myData1, myData2, myData3, myData4, myData5, myData6))
                

target1 = pickle.load( open( file_target1, "rb" ) )
target2 = pickle.load( open( file_target2, "rb" ) )
target3 = pickle.load( open( file_target3, "rb" ) )
target4 = pickle.load( open( file_target4, "rb" ) )
target5 = pickle.load( open( file_target5, "rb" ) )
target6 = pickle.load( open( file_target6, "rb" ) )


target = np.vstack((target1.reshape(-1,1),target2.reshape(-1,1),
                    target3.reshape(-1,1),target4.reshape(-1,1),target5.reshape(-1,1),
                    target6.reshape(-1,1)
                   ))

In [4]:
myData.shape, target.shape

((11608272, 109), (11608272, 1))

In [5]:
file_myData = "corrected_myDataFSUslipdevset.pickle"
file_target = "corrected_targetFSUslipdevset.pickle"
X_dev = pickle.load( open( file_myData, "rb" ) )
y_dev = pickle.load( open( file_target, "rb" ) )

In [6]:
X_train, y_train = shuffle(myData, target, random_state=0)

In [7]:
scaler = pickle.load( open( 'FSscale_version2', "rb" ) )
X_train_norm = scaler.transform(X_train)
X_dev_norm = scaler.transform(X_dev)

## Based on gradients

In [57]:
np.abs(np.array([-5,-5,-5]))

array([5, 5, 5])

In [67]:
def get_gradients(a):
    """Average first and last element of a 1-D array"""
    x_left   = np.hstack([a[0], a[3], a[6]])
    x_middle = np.hstack([a[1], a[4], a[7]])
    x_right  = np.hstack([a[2], a[5], a[8]])
    y_0 = a[1]
    y_first  = (x_right-x_left)
    y_second = (x_right-2*x_middle + x_left)
    return np.hstack([y_0, y_first, y_second])

def get_gradients_abs(a):
    """Average first and last element of a 1-D array"""
    x_left   = np.hstack([a[0], a[3], a[6]])
    x_middle = np.hstack([a[1], a[4], a[7]])
    x_right  = np.hstack([a[2], a[5], a[8]])
    y_0 = a[1]
    y_first  = np.abs(x_right-x_left)
    y_second = (x_right-2*x_middle + x_left)
    return np.hstack([y_0, y_first, y_second])

def get_gradients_second(a):
    """Average first and last element of a 1-D array"""
    x_left   = np.hstack([a[0], a[3], a[6]])
    x_middle = np.hstack([a[1], a[4], a[7]])
    x_right  = np.hstack([a[2], a[5], a[8]])
    y_0 = a[1]
    y_second = (x_right-2*x_middle + x_left)
    return np.hstack([y_0, y_second])

def get_gradients_first(a):
    """Average first and last element of a 1-D array"""
    x_left   = np.hstack([a[0], a[3], a[6]])
    x_middle = np.hstack([a[1], a[4], a[7]])
    x_right  = np.hstack([a[2], a[5], a[8]])
    y_0 = a[1]
    y_first  = (x_right-x_left)
    return np.hstack([y_0, y_first])

def get_gradients_first_abs(a):
    """Average first and last element of a 1-D array"""
    x_left   = np.hstack([a[0], a[3], a[6]])
    x_middle = np.hstack([a[1], a[4], a[7]])
    x_right  = np.hstack([a[2], a[5], a[8]])
    y_0 = a[1]
    y_first  = np.abs(x_right-x_left)
    return np.hstack([y_0, y_first])

def get_gradients_none(a):
    """Average first and last element of a 1-D array"""
    x_left   = np.hstack([a[0], a[3], a[6]])
    x_middle = np.hstack([a[1], a[4], a[7]])
    x_right  = np.hstack([a[2], a[5], a[8]])
    y_0 = a[1]
    y_first  = (x_right-x_left)
    return np.hstack([y_0])

def get_gradients_first3(a):
    """Average first and last element of a 1-D array"""
    x_left   = a[0]
    x_middle = a[1]
    x_right  = a[2]
    y_0 = a[1]
    y_first  = (x_right-x_left)
    return np.hstack([y_0, y_first])

In [49]:
newlist1 = []
newlist2 = []
newlist3 = []

index = 0
for i in range(-1,2):
    for j in range(-1,2):
        for k in range(-1,2):
            if (i == 0 and j == 0) or (i ==0 and k == 0) or (j == 0 and k == 0): 
                if i == 0 and j == 0:
                    newlist1.append(index)
                if i == 0 and k == 0:
                    newlist2.append(index)
                if j == 0 and k == 0:
                    newlist3.append(index)
            index +=1

newlist = newlist1 + newlist2 + newlist3
phis_index =  [4*x+1 for x in newlist]
vzs_index =   [4*x+4 for x in newlist]

phis_index3 =  [4*x+1 for x in newlist1]
vzs_index3 =   [4*x+4 for x in newlist1]

In [10]:
alist = []
index = 0
for i in range(-1,2):
    for j in range(-1,2):
        for k in range(-1,2):
            if (i == 0 and j == 0) or (i ==0 and k == 0) or (j == 0 and k == 0): 
                alist.append(index)
            index +=1
list_of_lists = [[4*x+1,4*x+4] for x in alist]
flattened = [0] + [val for sublist in list_of_lists for val in sublist] 
flattened

[0, 17, 20, 41, 44, 49, 52, 53, 56, 57, 60, 65, 68, 89, 92]

In [11]:
np.unique(phis_index + vzs_index)

array([17, 20, 41, 44, 49, 52, 53, 56, 57, 60, 65, 68, 89, 92])

In [12]:
phis_index, vzs_index

([49, 53, 57, 41, 53, 65, 17, 53, 89], [52, 56, 60, 44, 56, 68, 20, 56, 92])

In [43]:
phis_index3

[17, 53, 89]

In [68]:
def get_X_gradients(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients, 1, X[:,phis_index]), 
           np.apply_along_axis(get_gradients, 1, X[:,vzs_index])])

def get_X_gradients_abs(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients_abs, 1, X[:,phis_index]), 
           np.apply_along_axis(get_gradients_abs, 1, X[:,vzs_index])])

def get_X_gradients_second(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients_second, 1, X[:,phis_index]), 
           np.apply_along_axis(get_gradients_second, 1, X[:,vzs_index])])

def get_X_gradients_first(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients_first, 1, X[:,phis_index]), 
           np.apply_along_axis(get_gradients_first, 1, X[:,vzs_index])])

def get_X_gradients_first_abs(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients_first_abs, 1, X[:,phis_index]), 
           np.apply_along_axis(get_gradients_first_abs, 1, X[:,vzs_index])])

def get_X_gradients_none(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients_none, 1, X[:,phis_index]), 
           np.apply_along_axis(get_gradients_none, 1, X[:,vzs_index])])

def get_X_gradients_first3(X):
    return np.hstack([X[:,:1], np.apply_along_axis(get_gradients_first3, 1, X[:,phis_index3]), 
           np.apply_along_axis(get_gradients_first3, 1, X[:,vzs_index3])])

In [20]:
X_train_grad = get_X_gradients(X_train)
X_dev_grad = get_X_gradients(X_dev)


KeyboardInterrupt: 

In [23]:
X_train_grad_second = get_X_gradients_second(X_train)
X_dev_grad_second = get_X_gradients_second(X_dev)

In [18]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'one_gradients_full.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 33s - loss: 0.3481 - val_loss: 0.3479
Epoch 2/15
11608272/11608272 [==============================] - 41s - loss: 0.3390 - val_loss: 0.3417
Epoch 3/15
11608272/11608272 [==============================] - 36s - loss: 0.3351 - val_loss: 0.2588
Epoch 4/15
11608272/11608272 [==============================] - 39s - loss: 0.3326 - val_loss: 0.3124
Epoch 5/15
11608272/11608272 [==============================] - 37s - loss: 0.3318 - val_loss: 0.2598
Epoch 6/15
11608272/11608272 [==============================] - 38s - loss: 0.3311 - val_loss: 0.2859
Epoch 7/15
11608272/11608272 [==============================] - 36s - loss: 0.3307 - val_loss: 0.2852
Epoch 8/15
11608272/11608272 [==============================] - 33s - loss: 0.3304 - val_loss: 0.2951
Epoch 9/15
11608272/11608272 [==============================] - 32s - loss: 0.3302 - val_loss: 0.3598
Epoch 10/15
11608272/11608272

In [24]:
X_train_grad_second.shape[1]

9

In [26]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad_second.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'gradients_second.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad_second, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad_second, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 28s - loss: 0.3753 - val_loss: 0.2442
Epoch 2/15
11608272/11608272 [==============================] - 28s - loss: 0.3684 - val_loss: 0.3238
Epoch 3/15
11608272/11608272 [==============================] - 28s - loss: 0.3671 - val_loss: 0.3220
Epoch 4/15
11608272/11608272 [==============================] - 29s - loss: 0.3665 - val_loss: 0.3652
Epoch 5/15
11608272/11608272 [==============================] - 30s - loss: 0.3661 - val_loss: 0.3273
Epoch 6/15
11608272/11608272 [==============================] - 30s - loss: 0.3658 - val_loss: 0.3052
Epoch 7/15
11608272/11608272 [==============================] - 30s - loss: 0.3656 - val_loss: 0.3302
Epoch 8/15
11608272/11608272 [==============================] - 30s - loss: 0.3655 - val_loss: 0.3510
Epoch 9/15
11608272/11608272 [==============================] - 30s - loss: 0.3653 - val_loss: 0.3258
Epoch 10/15
11608272/11608272

In [29]:
X_train_grad_first = get_X_gradients_first(X_train)
X_dev_grad_first = get_X_gradients_first(X_dev)

In [30]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad_first.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'gradients_first.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad_first, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad_first, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 33s - loss: 0.3550 - val_loss: 0.2225
Epoch 2/15
11608272/11608272 [==============================] - 31s - loss: 0.3447 - val_loss: 0.2851
Epoch 3/15
11608272/11608272 [==============================] - 32s - loss: 0.3426 - val_loss: 0.2627
Epoch 4/15
11608272/11608272 [==============================] - 32s - loss: 0.3415 - val_loss: 0.2676
Epoch 5/15
11608272/11608272 [==============================] - 32s - loss: 0.3410 - val_loss: 0.3255
Epoch 6/15
11608272/11608272 [==============================] - 35s - loss: 0.3405 - val_loss: 0.3262
Epoch 7/15
11608272/11608272 [==============================] - 34s - loss: 0.3402 - val_loss: 0.3519
Epoch 8/15
11608272/11608272 [==============================] - 37s - loss: 0.3399 - val_loss: 0.3457
Epoch 9/15
11608272/11608272 [==============================] - 31s - loss: 0.3397 - val_loss: 0.3822
Epoch 10/15
11608272/11608272

In [35]:
X_train_grad_none = get_X_gradients_none(X_train)
X_dev_grad_none = get_X_gradients_none(X_dev)

In [36]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad_none.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'gradients_none.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad_none, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad_none, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 29s - loss: 0.3896 - val_loss: 0.2719
Epoch 2/15
11608272/11608272 [==============================] - 25s - loss: 0.3860 - val_loss: 0.2920
Epoch 3/15
11608272/11608272 [==============================] - 25s - loss: 0.3852 - val_loss: 0.5202
Epoch 4/15
11608272/11608272 [==============================] - 29s - loss: 0.3849 - val_loss: 0.3230
Epoch 5/15
11608272/11608272 [==============================] - 30s - loss: 0.3847 - val_loss: 0.4191
Epoch 6/15
11608272/11608272 [==============================] - 28s - loss: 0.3843 - val_loss: 0.3256
Epoch 7/15
11608272/11608272 [==============================] - 28s - loss: 0.3838 - val_loss: 0.3437
Epoch 8/15
11608272/11608272 [==============================] - 29s - loss: 0.3837 - val_loss: 0.3983
Epoch 9/15
11608272/11608272 [==============================] - 26s - loss: 0.3835 - val_loss: 0.3404
Epoch 10/15
11608272/11608272

In [52]:
X_train_grad_first3 = get_X_gradients_first3(X_train)
X_dev_grad_first3 = get_X_gradients_first3(X_dev)

In [53]:
X_train_grad_first3.shape

(11608272, 5)

In [54]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad_first3.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'gradients_first3.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad_first3, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad_first3, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 27s - loss: 0.3834 - val_loss: 0.2552
Epoch 2/15
11608272/11608272 [==============================] - 26s - loss: 0.3780 - val_loss: 0.2930
Epoch 3/15
11608272/11608272 [==============================] - 26s - loss: 0.3766 - val_loss: 0.3366
Epoch 4/15
11608272/11608272 [==============================] - 27s - loss: 0.3760 - val_loss: 0.3358
Epoch 5/15
11608272/11608272 [==============================] - 27s - loss: 0.3756 - val_loss: 0.3631
Epoch 6/15
11608272/11608272 [==============================] - 27s - loss: 0.3753 - val_loss: 0.3287
Epoch 7/15
11608272/11608272 [==============================] - 27s - loss: 0.3751 - val_loss: 0.3370
Epoch 8/15
11608272/11608272 [==============================] - 27s - loss: 0.3749 - val_loss: 0.3624
Epoch 9/15
11608272/11608272 [==============================] - 27s - loss: 0.3748 - val_loss: 0.3806
Epoch 10/15
11608272/11608272

In [ ]:
X_train_grad_abs = get_X_gradients_abs(X_train)
X_dev_grad_abs = get_X_gradients_abs(X_dev)

In [62]:
X_train_grad_abs.shape, X_dev_grad_abs.shape

((11608272, 15), (77389, 15))

In [64]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad_abs.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'gradients_full_abs.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad_abs, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad_abs, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 33s - loss: 0.3444 - val_loss: 0.3523
Epoch 2/15
11608272/11608272 [==============================] - 36s - loss: 0.3333 - val_loss: 0.3580
Epoch 3/15
11608272/11608272 [==============================] - 33s - loss: 0.3311 - val_loss: 0.3713
Epoch 4/15
11608272/11608272 [==============================] - 34s - loss: 0.3303 - val_loss: 0.3784
Epoch 5/15
11608272/11608272 [==============================] - 39s - loss: 0.3298 - val_loss: 0.3498
Epoch 6/15
11608272/11608272 [==============================] - 35s - loss: 0.3294 - val_loss: 0.3331
Epoch 7/15
11608272/11608272 [==============================] - 33s - loss: 0.3292 - val_loss: 0.3215
Epoch 8/15
11608272/11608272 [==============================] - 39s - loss: 0.3290 - val_loss: 0.2968
Epoch 9/15
11608272/11608272 [==============================] - 39s - loss: 0.3288 - val_loss: 0.2963
Epoch 10/15
11608272/11608272

In [69]:
X_train_grad_first_abs = get_X_gradients_first_abs(X_train)
X_dev_grad_first_abs = get_X_gradients_first_abs(X_dev)

In [70]:
X_train_grad_first_abs.shape, X_dev_grad_first_abs.shape

((11608272, 9), (77389, 9))

In [ ]:
model = Sequential()
model.add(Dense(100, activation='relu', kernel_initializer='normal',input_dim=X_train_grad_first_abs.shape[1]))
model.add(Dense(1, activation='linear', kernel_initializer='normal'))
adam = optimizers.Adam(lr=0.01)
model.compile(loss='mean_absolute_error', optimizer=adam)
save_file = 'gradients_first_abs.hdf5'
#model.load_weights(save_file)
checkpointer = ModelCheckpoint(filepath=save_file, verbose=1, save_best_only=True)
model.fit(X_train_grad_first_abs, y_train, batch_size=512, epochs=15, verbose=1, validation_data=(X_dev_grad_first_abs, y_dev), callbacks=[checkpointer])

Train on 11608272 samples, validate on 77389 samples
Epoch 1/15
11608272/11608272 [==============================] - 28s - loss: 0.3539 - val_loss: 0.2285
Epoch 2/15
11608272/11608272 [==============================] - 28s - loss: 0.3459 - val_loss: 0.2760
Epoch 3/15
11608272/11608272 [==============================] - 28s - loss: 0.3445 - val_loss: 0.2638
Epoch 4/15
11608272/11608272 [==============================] - 29s - loss: 0.3436 - val_loss: 0.4012
Epoch 5/15
11608272/11608272 [==============================] - 29s - loss: 0.3432 - val_loss: 0.2856
Epoch 6/15
11608272/11608272 [==============================] - 29s - loss: 0.3429 - val_loss: 0.2833
Epoch 7/15
11608272/11608272 [==============================] - 29s - loss: 0.3426 - val_loss: 0.3093
Epoch 8/15
11608272/11608272 [==============================] - 29s - loss: 0.3424 - val_loss: 0.3499
Epoch 9/15
11608272/11608272 [==============================] - 29s - loss: 0.3422 - val_loss: 0.3501
Epoch 10/15
11608272/11608272